# Baseline
Setting up a more robust baseline notebook, suitable for use with all of the "Big Three" (XGBoost, CatBoost, LightGBM) libraries and on either Google Colab or the local machine.

# Setup

In [1]:
# two manual flags (ex-config)
colab = False
gpu_available = False

In [2]:
# basic imports
from pathlib import Path
import os
import math
from datetime import datetime

In [3]:
%matplotlib inline
%config Completer.use_jedi = False
os.environ['WANDB_NOTEBOOK_NAME'] = f"sweep_lightgbm_{datetime.now().strftime('%Y%m%d')}.ipynb"

In [4]:
# handle Google Colab-specific library installation/updating
if colab:
    # much of the below inspired by or cribbed from the May 2021 Kaggle Tabular Playground winner, at 
    # https://colab.research.google.com/gist/academicsuspect/0aac7bd6e506f5f70295bfc9a3dc2250/tabular-may-baseline.ipynb?authuser=1#scrollTo=LJoVKJb5wN0L
    
    # Kaggle API for downloading the datasets
    !pip install --upgrade -q kaggle

    # weights and biases
    !pip install -qqqU wandb
    
    # Optuna for parameter search
    !pip install -q optuna

    !pip install --upgrade xgboost

    # upgrade sklearn
    !pip install --upgrade scikit-learn

    !pip install category_encoders
    !pip install catboost

    # lighgbm gpu compatible
    !git clone --recursive https://github.com/Microsoft/LightGBM
    ! cd LightGBM && rm -rf build && mkdir build && cd build && cmake -DUSE_GPU=1 ../../LightGBM && make -j4 && cd ../python-package && python3 setup.py install --precompile --gpu;
    
    # this part is from https://github.com/rapidsai/gputreeshap/issues/24
    !pip install cmake --upgrade
    # !pip install sklearn --upgrade
    !git clone --recursive https://github.com/dmlc/xgboost
    %cd /content/xgboost
    !mkdir build
    %cd build
    !cmake .. -DUSE_CUDA=ON
    !make -j4
    %cd /content/xgboost/python-package
    !python setup.py install --use-cuda --use-nccl
    !/opt/bin/nvidia-smi
    !pip install shap
    

Now, non-stdlib imports

In [5]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm.notebook import tqdm

# general ML tooling
from sklearn.model_selection import train_test_split, StratifiedKFold, KFold
from sklearn.metrics import log_loss, roc_auc_score
import wandb
from wandb.xgboost import wandb_callback
from wandb.lightgbm import wandb_callback
from sklearn.impute import KNNImputer
# import timm

import seaborn as sns

from catboost import CatBoostClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
# from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import MaxAbsScaler, StandardScaler, MinMaxScaler, RobustScaler, PolynomialFeatures
# from sklearn.feature_selection import SelectKBest, f_regression
from joblib import dump, load
# feature engineering tools
# from sklearn.feature_selection import mutual_info_regression
# import featuretools as ft


Now, datapath setup

In [6]:
# # This is the code for reading the train.csv and converting it to a .feather file
# df = pd.read_csv(datapath/'train.csv', index_col='id', low_memory=False)
# df.index.name = None
# df.to_feather(path='./dataset_df.feather')

In [7]:
if colab:
    # mount Google Drive
    from google.colab import drive
    drive.mount('/content/drive')
    
    # handling datapath
    datapath = Path('/content/drive/MyDrive/kaggle/tabular_playgrounds/sep2021/')
    
else:
    # if on local machine
    datapath = Path('/media/sf/easystore/kaggle_data/tabular_playgrounds/sep2021/')    
    


## Ex-Model Config

In [8]:
# meta-config for preprocessing and cross-validation, but NOT for model parameters
# in the sweep version, this includes both ex-model parameters and defaults for model parameters
config_defaults = {
    # model config
    "library": 'lightgbm',
#     "model": XGBClassifier,
#     "n_estimators": 100, 
#     "max_depth": 3,
#     "learning_rate": 0.1,
#     "test_size": 0.2,
#     "reg_lambda": None, 
    "scaler": MinMaxScaler, # TODO: experiment with others (but imputation may be slow)
    "scale_b4_impute": None,
    "imputer": None,
    "knn_imputer_n_neighbors": None, # None if a different imputer is used
#     "feature_selector": SelectKBest,
#     "k_best": 80,
#     "feature_selection_scoring": f_regression,
    'random_state': 42,
#     'subsample': 1,
    'cross_val_strategy': None, # None for holdout, or the relevant sklearn class
    'kfolds': 1, # if 1, that means just doing holdout
    'test_size': 0.2,
    # these are XGBoost default (my choice) params 
    "tree_method": "auto", # set to 'gpu_hist' to try GPU if available
    "booster": 'gbtree', # dart may be marginally better, but will opt for this quicker approach as a default
    "n_estimators": 200, 
    "max_depth": 3,
    "learning_rate": 0.1,
    "n_jobs": -1,
    "verbosity": 1,
    "subsample": 1,
#     'features_created': False,
#     'feature_creator': None,
}

## Data Setup

**TODO** Write some conditional logic here to automate it -- possibly as part of a sklearn.*pipeline

In [9]:
# if exmodel_config['scaler']:
#     scaler = exmodel_config['scaler']()
#     scaler.fit_transform()

In [10]:
# # here's how to load the original, unaltered dataset and separate features from targets
# df = pd.read_feather(path=datapath/'dataset_df.feather') # this is the unaltered original dataset
# features = [x for x in df.columns if x != 'claim']
# X = df[features]
# y = df.claim

# load the version of the dataset with imputations; X and y were stored separately, as feather and joblib respectively
# X = pd.read_feather(datapath/'X_StandardScaled_KNNImputed_5NN.feather') 
# y = load(datapath/'y.joblib')    
# X.index.name = 'id'
# y.index.name = 'id'

In [11]:
# scaler = exmodel_config['scaler']()
# X_scaled = scaler.fit_transform(X)
# X = pd.DataFrame(X_scaled, columns=X.columns)

In [12]:
# X.head()

In [13]:
# y.head()

## Sweep Config

In [14]:
# XGBOOST
sweep_config = {
    "method": "bayes", # try grid or random
    "metric": {
      "name": "auc",
      "goal": "maximize"   
    },
    "parameters": {
        "max_depth": {
            "distribution": "int_uniform", 
            "min": 2,
            "max": 5,
        },
        "learning_rate": {
            "distribution": "uniform", 
            "min": 0.001,
            "max": 0.4
            #             "values": [0.1, 0.2, 0.3]
        },
        "n_estimators": {
            "distribution": "int_uniform",
            "min": 100,
            "max": 2000,
#             "values": [50, 125, 200]
        },
#         "scaler": {
#             "distribution": "constant",
#             "values": [MaxAbsScaler, StandardScaler, MinMaxScaler, RobustScaler],
#         },
        "reg_alpha": {
            "distribution": "uniform",
            "min": 0,
            "max": 4,
        },
        "reg_lambda": {
            "distribution": "uniform",
            "min": 0,
            "max": 5,
        },
        "subsample": {
            "distribution": "uniform",
            "min": 0.6,
            "max": 1,
        }
    }
}

### Model Config

In [15]:
def model_configurator(library, gpu_available=True):#, config=universal_config):
    """
    Function that provide task-specific or general preference arguments for the various models. 
    
    At first, will rely largely on defaults for hyperparameters, but later this function 
    can be supplemented later with optimal values, as they're learned in sweeps.
    .
    
    Rationale: creating a helper function will allow more experimentation later, and also
    composite runs that cycle through a series of models.
    
    :param model: A model from [XGBClassifier, LGBMClassifier, CatBoostClassifier]
    :return config: A dict that supplements default hyperparameter values with 1) 
                    task-appropriate ones, and perhaps later 2) optimal hyperparameter values.
    """
    config = {}
#     if library == 'xgboost':
#         config['model'] = XGBClassifier()
#     elif library == 'lightgbm':
#         config['model'] = LGBMClassifier()
#     elif library == 'catboost':
#         config['model'] = CatBoostClassifier()
#     else:
#         print("Invalid library")
#         return None
    
    # library-specific config
#     if config['model'] in [XGBClassfier, LGBMClassifier]:
    if library in ['xgboost', 'lightgbm']:
#         config['reg_alpha'] = None
        config['n_jobs'] = -1
        

#     if config['model'] == XGBClassifier:
    if library == 'xgboost':
#         config['tree_method'] = 'auto'
#         config['booster'] = 'gbtree' # or 'dart'
#         config['model'] = XGBClassifier
        config['verbosity'] = 1
        config['objective'] = 'binary:logistic'
#         config['eval_metric'] = ['auc', 'logloss', 'aucpr'],
#         config['eval_metric'] = 'logloss',
        config['tree_method'] = 'gpu_hist' if (gpu_available and colab) else 'auto' 
#         config['reg_alpha'] = 
#         config['n_estimators'] = 300

#     if config['model'] == LGBMClassifier:
    if library == 'lightgbm':
#         config['model'] = LGBMClassifier
        config['objective'] = 'binary'
        config['eval_metric'] = ['auc', 'logloss']
        config['boosting_type'] = 'gbdt' # or 'dart'
        config['device_type'] = 'cuda' if (gpu_available and colab) else 'cpu' # 'gpu' also possible, 'cpu' is default
        config['n_estimators'] = 500

#     if config['model'] == CatBoostClassifier:
    if library == 'catboost':
#         config['model'] = CatBoostClassifier
        config['task_type'] = 'GPU' if gpu_available else 'CPU'
        config['custom_metrics'] = ['Logloss', 'AUC'] # objective (loss fn) must be singular, defaults to Logloss
        config['n_estimators'] = 2000 # logged as "iterations" otherwise

    return config

## Weights and Biases Run Config

Below is the configuration for a Weights and Biases (`wandb`) run.

In [16]:
config_run = {
    # wandb config:
    'name': f"{os.environ['WANDB_NOTEBOOK_NAME'][:-6]}_{datetime.now().strftime('%H%M%S')}", # just removes the .ipynb extension, leaving the notebook filename's stem
    'tags': ['sweep'],
    'notes': "Sweep for LightGBM, with scaling but no imputation or feature generation/selection",
}

# Preprocessing
Scaling has already occurred -- used `StandardScaler` as a precursor to using `KNNImputer(n_neighbors=5)`, on the premise that imputation would proceed more quickly if things were already scaled. I may try different permutations of this later: using `IterativeImputer` instead, before or after scaling, potentially with different scalers. 

# Feature Creation and Selection

In [17]:
# load all the polynomialfeatures generated with `PolynomialFeatures(degree=2, include_bias=True, interaction_only=False)`
# X_np = np.load(datapath/'X_poly_unscaled.npy')
# X = pd.DataFrame(X_np)

In [18]:
# X.columns

In [19]:
# generation polynomial features
# poly = PolynomialFeatures(degree=2, include_bias=True, interaction_only=False)
# X_poly = poly.fit_transform(X)

In [20]:
# X_poly_names = poly.get_feature_names(X.columns)
# # X_poly_names[100:150]
# features = pd.read_csv('X_candidates_20210827.csv').columns

In [21]:
# checks = [feature in X_poly_names for feature in features]
# checks

In [22]:
# X = pd.DataFrame(X_poly, columns=X_poly_names)

In [23]:
# X = X[features[1:]]

# Training

In [24]:
# def train(X_train, X_valid, y_train, y_valid, model_config, 
#                                               random_state=42,
#                                               exmodel_config=exmodel_config, 
#                                               config_run=config_run):#, scaler): # passed in via config dict for now
#     """
#     Basic training function. Note that some of the options passed via the argument are
#     in fact hard-coded in, to avoid inconveniences.
#     :param X_train: the training set features
#     :param X_valid: the validation set features
#     :param y_train: the training set targets
#     :param y_valid: the validation set targets
#     :param random_staKFold: for reproducibility
#     :param exmodel_config: dict containing configuration details including the library 
#                             (thus model) used, preprocessing, and cross-validation
#     :param model_config: dict containing hyperparameter specifications for the model
#     :param config_run: dict containing wandb run configuration (name, etc)
#     """
    
    
#     wandb.init(
#         project="202109_Kaggle_tabular_playground",
#         save_code=True,
#         tags=config_run['tags'],
#         name=config_run['name'],
#         notes=config_run['notes'],
#         config=exmodel_config)   
        
#     if exmodel_config['library'] == 'xgboost':
#         model = XGBClassifier(
# #             tree_method=config['tree_method'],
# #             booster=config['booster'],
# #             n_estimators=config['n_estimators'], 
# #             max_depth=config['max_depth'],
# #             learning_rate=config['learning_rate'], 
# #             subsample=config['subsample'],
# #             reg_alpha=config['reg_alpha'],
# #             reg_lambda=config['reg_lambda'],
#             random_state=random_state,
#             n_jobs=model_config['n_jobs'], 
#             verbosity=model_config['verbosity'], 
#             objective=model_config['objective'],
# #             eval_metric=model_config['eval_metric'],
#             tree_method=model_config['tree_method'],
#             n_estimators=model_config['n_estimators'],
#         )
        
#         model.fit(X_train, y_train, callbacks=[wandb.xgboost.wandb_callback()],
# #                                     eval_metric=model_config['eval_metric'],
#                  )


#     elif exmodel_config['library'] == 'lightgbm':
#         model = LGBMClassifier(
# #             boosting_type=model_config['boosting_type'],
# #             max_depth=model_config['max_depth']
#             # TODO
#             random_state=random_state,
#             n_jobs=model_config['n_jobs'],
#             objective=model_config['objective'],
#             eval_metric=model_config['eval_metric'],
#             boosting_type=model_config['boosting_type'],
#             device_type=model_config['device_type'],
#             n_estimators=model_config['n_estimators'],

#         )
        
#         model.fit(X_train, y_train, callbacks=[wandb.lightgbm.wandb_callback()],
# #                                     eval_metric=model_config['eval_metric'],
#                  )
        
#     elif exmodel_config['library'] == 'catboost':
#         print("CatBoost, therefore no WandB callback.")
#         model = CatBoostClassifier(
# #             n_estimators=config['n_estimators'],
# #             learning_rate=config['learning_rate'],
# #             max_depth=config['max_depth'],
#             task_type=model_config['task_type'],
#     #         n_jobs=config['n_jobs'],
#     #         verbosity=config['verbosity'],
#     #         subsample=config['subsample'],
#             n_estimators=model_config['n_estimators'],
#             random_state=random_state,
#             # objective='Logloss', # default, accepts only one
# #             custom_metrics=model_config['custom_metrics'],
#     #         bootstrap_type=config['bootstrap_type'],
#     #         device:config['device']
#         ) 
#         model.fit(X_train, y_train)
#     y_train_pred = model.predict(X_train)
#     train_loss = log_loss(y_train, y_train_pred)
#     train_auc = roc_auc_score(y_train, y_train_pred)
#     wandb.log({'train_loss': train_loss, 'train_auc': train_auc})

#     if exmodel_config['library'] == 'catboost':
#         print(model.get_all_params())
#         wandb.log(model.get_all_params())
#     else:
#         wandb.log(model.get_params()) # logging model parameters, trying bare-invocation rather than params: model.get_params()
    
#     y_pred = model.predict(X_valid)
# #     mse = mean_squared_error(y_valid, y_pred)
# #     rmse = math.sqrt(abs(mse))
#     valid_loss = log_loss(y_valid, y_pred)
#     valid_auc = roc_auc_score(y_valid, y_pred)
#     wandb.log({'valid_loss':valid_loss, 'valid_auc':valid_auc})
#     print(f"Valid log-loss is {valid_loss}\nValid AUC is {valid_auc}")   
# #     wandb.finish()   
#     return model
    

In [25]:
def train_lightgbm_sweep():
    """
    Sweep training function. No parameters.
    """
    
    wandb.init(
        tags=config_run['tags'],
        name=config_run['name'],
        notes=config_run['notes'],
        config=config_defaults)   
        
    config = wandb.config
    # putting all the data extraction, scaling, splitting here
    datapath = Path('/media/sf/easystore/kaggle_data/tabular_playgrounds/sep2021/')    
    df = pd.read_feather(path=datapath/'dataset_df.feather') # this is the unaltered original dataset
    features = [x for x in df.columns if x != 'claim']
    X = df[features]
    y = df.claim
    scaler = MinMaxScaler()
    X_scaled = scaler.fit_transform(X)
    X = pd.DataFrame(X_scaled, columns=X.columns)    
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, 
                                                      test_size=config['test_size'], 
                                                      random_state=config['random_state'],
                                                     )
    # parallel this for other libraries
    model = LGBMClassifier(
#         tree_method=config['tree_method'],
#         booster=config['booster'],
        n_estimators=config['n_estimators'], 
        max_depth=config['max_depth'],
        learning_rate=config['learning_rate'], 
        reg_alpha=config['reg_alpha'],
        reg_lambda=config['reg_lambda'],
        subsample=config['subsample'],
        random_state=config['random_state'],
        n_jobs=config['n_jobs'], 
#         verbosity=config['verbosity'], 
    )
#             random_state=random_state,
#             n_jobs=model_config['n_jobs'], 
#             verbosity=model_config['verbosity'], 
#             objective=model_config['objective'],
#             tree_method=model_config['tree_method'],
#             n_estimators=model_config['n_estimators'],
    model.fit(X_train, y_train, callbacks=[wandb.lightgbm.wandb_callback()],
#                                     eval_metric=model_config['eval_metric'],
             )

    y_train_pred = model.predict(X_train)
    train_loss = log_loss(y_train, y_train_pred)
    train_auc = roc_auc_score(y_train, y_train_pred)
    wandb.log({'train_loss': train_loss, 'train_auc': train_auc})

    wandb.log(model.get_params()) # logging model parameters, trying bare-invocation rather than params: model.get_params()
    
    y_pred = model.predict(X_valid)
#     mse = mean_squared_error(y_valid, y_pred)
#     rmse = math.sqrt(abs(mse))
    valid_loss = log_loss(y_valid, y_pred)
    valid_auc = roc_auc_score(y_valid, y_pred)
    wandb.log({'valid_loss':valid_loss, 'valid_auc':valid_auc})
    print(f"Valid log-loss is {valid_loss}\nValid AUC is {valid_auc}")   
#     wandb.finish()   
#     return model
    

In [26]:
# def cross_validation(model_config, X=X, y=y, start_fold=0, exmodel_config=exmodel_config, random_state=42):
#     """
#     Function to handle model training process in the context of cross-validation -- via hold-out or via k-fold.
#     If exmodel_config['cross_val_strategy'] == None, then any kfolds= input is ignored; otherwise, the number specified is used.
    
#     :param kfolds: int specifying number of k-folds to use in cross-validation
#     :param exmodel_config: dict containing general config including for cross-validation -- `kfold=1` implies hold-out
#     """
#     if exmodel_config['kfolds'] == 1:
#         print("Proceeding with holdout")
#         X_train, X_valid, y_train, y_valid = train_test_split(X, y, 
#                                                       test_size=exmodel_config['test_size'], 
#                                                       random_state=random_state,
#                                                      )
#         model = train(X_train, X_valid, y_train, y_valid, exmodel_config=exmodel_config, 
#                                                     model_config=model_config,
#                                                     config_run=config_run)
#         wandb.finish()
        
#     else:
#         X, y = X.to_numpy(), y.to_numpy()
#         kfold = exmodel_config['cross_val_strategy'](n_splits=exmodel_config['kfolds'], shuffle=True, random_state=random_state)
#         models = {}
#         model_path = Path(datapath/f"models/{config_run['name']}_{exmodel_config['kfolds']}folds/")
#         (model_path).mkdir(exist_ok=True)
#         for fold, (train_ids, valid_ids) in enumerate(kfold.split(X,y)):
#             if fold < start_fold:
#                 continue
#             else:
#                 print(f"FOLD {fold}")
#                 print("---------------------------------------------------")
#                 X_train, X_valid = X[train_ids], X[valid_ids]
#                 y_train, y_valid = y[train_ids], y[valid_ids]
#                 model = train(X_train, X_valid, y_train, y_valid, exmodel_config=exmodel_config, 
#                                                     model_config=model_config,
#                                                     config_run=config_run)
#                 wandb.log({'fold': fold})
#                 models[fold] = model
#                 dump(model, Path(model_path/f"{exmodel_config['library']}_fold{fold}_model.joblib"))
#                 wandb.finish()
#         return models
        

# Interface

## Hyperparameter Sweep

In [27]:
sweep_id = wandb.sweep(sweep_config, project="202109_Kaggle_tabular_playground")

Create sweep with ID: sjghewf0
Sweep URL: https://wandb.ai/hushifang/202109_Kaggle_tabular_playground/sweeps/sjghewf0


In [28]:
wandb.agent(sweep_id, train_lightgbm_sweep)

wandb: Agent Starting Run: c39n6z1i with config:
wandb: 	learning_rate: 0.2581240982248908
wandb: 	max_depth: 3
wandb: 	n_estimators: 1138
wandb: 	reg_alpha: 1.54583767847818
wandb: 	reg_lambda: 2.837260707418631
wandb: 	subsample: 0.852923116174515
wandb: Currently logged in as: hushifang (use `wandb login --relogin` to force relogin)


Valid log-loss is 9.1693134543656
Valid AUC is 0.734358038643559


wandb: Agent Starting Run: 9tfynlih with config:
wandb: 	learning_rate: 0.009498966185640653
wandb: 	max_depth: 5
wandb: 	n_estimators: 324
wandb: 	reg_alpha: 2.5284090963811567
wandb: 	reg_lambda: 1.404782405385077
wandb: 	subsample: 0.7455484353702347


Valid log-loss is 9.50030488229677
Valid AUC is 0.7247123606356691


wandb: Agent Starting Run: iu82woz4 with config:
wandb: 	learning_rate: 0.025254829455835383
wandb: 	max_depth: 2
wandb: 	n_estimators: 1771
wandb: 	reg_alpha: 0.9748529496008214
wandb: 	reg_lambda: 0.19644902840011857
wandb: 	subsample: 0.6515361557526224


...

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: enffbobx with config:
wandb: 	learning_rate: 0.0524520279659399
wandb: 	max_depth: 3
wandb: 	n_estimators: 1393
wandb: 	reg_alpha: 2.980674717316488
wandb: 	reg_lambda: 0.15569537146374213
wandb: 	subsample: 0.9834793539890017


Valid log-loss is 9.069618602244335
Valid AUC is 0.7372556560487862


wandb: Agent Starting Run: cp1f4u19 with config:
wandb: 	learning_rate: 0.35997097767382774
wandb: 	max_depth: 2
wandb: 	n_estimators: 1861
wandb: 	reg_alpha: 3.9167312679125237
wandb: 	reg_lambda: 1.1922493226122306
wandb: 	subsample: 0.8239808482574756


Valid log-loss is 9.17922814437395
Valid AUC is 0.734063144866383


wandb: Sweep Agent: Waiting for job.
wandb: Sweep Agent: Exiting.


### Clean-up of config params


In [29]:
api = wandb.Api()

In [30]:
sweep = api.sweep("hushifang/202109_Kaggle_tabular_playground/sweeps/icac24c5/")

In [32]:
sweep.config["library"] = "lightgbm"

/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/wandb/apis/public.py:1554: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  return yaml.load(self._attrs["config"])


In [34]:
list(sweep.runs)

[<Run hushifang/202109_Kaggle_tabular_playground/loyoxhsd (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/r266xje4 (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/haq2vtz1 (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/2xyi4yru (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/9znenwmb (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/7wqrj0q2 (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/q3fhh270 (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/i648zona (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/5dk8g8kl (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/h340hhh2 (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/ua9ojo7h (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/57vmh6ck (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/3nzy8hoa (finished)>,
 <Run hushifang/202109_Kaggle_tabular_playground/rwij4v48 (finished)>,
 <Run 

In [40]:
for run in sweep.runs:
    print(str(run)[5:-12])

hushifang/202109_Kaggle_tabular_playground/loyoxhsd
hushifang/202109_Kaggle_tabular_playground/r266xje4
hushifang/202109_Kaggle_tabular_playground/haq2vtz1
hushifang/202109_Kaggle_tabular_playground/2xyi4yru
hushifang/202109_Kaggle_tabular_playground/9znenwmb
hushifang/202109_Kaggle_tabular_playground/7wqrj0q2
hushifang/202109_Kaggle_tabular_playground/q3fhh270
hushifang/202109_Kaggle_tabular_playground/i648zona
hushifang/202109_Kaggle_tabular_playground/5dk8g8kl
hushifang/202109_Kaggle_tabular_playground/h340hhh2
hushifang/202109_Kaggle_tabular_playground/ua9ojo7h
hushifang/202109_Kaggle_tabular_playground/57vmh6ck
hushifang/202109_Kaggle_tabular_playground/3nzy8hoa
hushifang/202109_Kaggle_tabular_playground/rwij4v48
hushifang/202109_Kaggle_tabular_playground/cxiqa8px
hushifang/202109_Kaggle_tabular_playground/55hxnnoj
hushifang/202109_Kaggle_tabular_playground/o2dgatsy
hushifang/202109_Kaggle_tabular_playground/1gilnmf6
hushifang/202109_Kaggle_tabular_playground/e7j3vsgi
hushifang/20

In [41]:
for x in sweep.runs:
    run_name = str(x)[5:-12]
    run = api.run(run_name)
    run.config['library'] = 'xgboost'
    run.update()

## Runs

In [34]:
library = 'xgboost'
exmodel_config['library'] = library
model_config = model_configurator(library)
xgboost_models = cross_validation(model_config)

FOLD 0
---------------------------------------------------


/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/training.py:17: UserWarning: Old style callback is deprecated.  See: https://xgboost.readthedocs.io/en/latest/python/callbacks.html
  warnings.warn(f'Old style callback is deprecated.  See: {link}', UserWarning)


Valid log-loss is 9.182656366311678
Valid AUC is 0.7339909390942767


FOLD 1
---------------------------------------------------


/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/training.py:17: UserWarning: Old style callback is deprecated.  See: https://xgboost.readthedocs.io/en/latest/python/callbacks.html
  warnings.warn(f'Old style callback is deprecated.  See: {link}', UserWarning)


...

Valid log-loss is 9.160840850471198
Valid AUC is 0.7347094322023537


FOLD 4
---------------------------------------------------


/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/sklearn.py:1146: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/training.py:17: UserWarning: Old style callback is deprecated.  See: https://xgboost.readthedocs.io/en/latest/python/callbacks.html
  warnings.warn(f'Old style callback is deprecated.  See: {link}', UserWarning)


Valid log-loss is 9.105002088717281
Valid AUC is 0.736265741386542


{0: XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
               colsample_bynode=1, colsample_bytree=1, gamma=0, gpu_id=-1,
               importance_type='gain', interaction_constraints='',
               learning_rate=0.300000012, max_delta_step=0, max_depth=6,
               min_child_weight=1, missing=nan, monotone_constraints='()',
               n_estimators=300, n_jobs=-1, num_parallel_tree=1, random_state=42,
               reg_alpha=0, reg_lambda=1, scale_pos_weight=1, subsample=1,
               tree_method='auto', validate_parameters=1, verbosity=1),
 1: XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
               colsample_bynode=1, colsample_bytree=1, gamma=0, gpu_id=-1,
               importance_type='gain', interaction_constraints='',
               learning_rate=0.300000012, max_delta_step=0, max_depth=6,
               min_child_weight=1, missing=nan, monotone_constraints='()',
               n_estimators=300, n_jobs=-1, n

In [ ]:
# for scaler in [StandardScaler, MaxAbsScaler, MinMaxScaler, RobustScaler]:
#     exmodel_config['scaler'] = scaler
#     scaler = scaler()
#     X_scaled = scaler.fit_transform(X)
#     X = pd.DataFrame(X_scaled, columns=X.columns)
#     exmodel_config['library'] = 'lightgbm'
#     model_config = model_configurator('lightgbm')
#     cross_validation(model_config)

In [35]:
# library = 'xgboost'
# exmodel_config['library'] = library
# model_config = model_configurator(library)
# xgboost_models = cross_validation(model_config)

library = 'lightgbm'
exmodel_config['library'] = library
model_config = model_configurator(library)
lightgbm_models = cross_validation(model_config)

library = 'catboost'
gpu_available = True
exmodel_config['library'] = library
model_config = model_configurator(library)
catboost_models = cross_validation(model_config)

FOLD 0
---------------------------------------------------


[LightGBM] [Warning] Unknown parameter: eval_metric
Valid log-loss is 8.649753788149516
Valid AUC is 0.7495285330622696


FOLD 1
---------------------------------------------------


[LightGBM] [Warning] Unknown parameter: eval_metric
Valid log-loss is 8.571151211404626
Valid AUC is 0.7517893500774024


FOLD 2
---------------------------------------------------


...

CatBoost, therefore no WandB callback.
Learning rate set to 0.012572
0:	learn: 0.6928163	total: 11.1ms	remaining: 22.3s
1:	learn: 0.6924804	total: 22ms	remaining: 21.9s
2:	learn: 0.6921627	total: 32.6ms	remaining: 21.7s
3:	learn: 0.6918395	total: 43.2ms	remaining: 21.6s
4:	learn: 0.6915186	total: 53.8ms	remaining: 21.5s
5:	learn: 0.6911996	total: 64.5ms	remaining: 21.4s
6:	learn: 0.6908838	total: 75.1ms	remaining: 21.4s
7:	learn: 0.6905652	total: 87ms	remaining: 21.7s
8:	learn: 0.6902511	total: 98ms	remaining: 21.7s
9:	learn: 0.6899327	total: 109ms	remaining: 21.6s
10:	learn: 0.6896204	total: 119ms	remaining: 21.6s
11:	learn: 0.6893110	total: 129ms	remaining: 21.5s
12:	learn: 0.6890027	total: 139ms	remaining: 21.3s
13:	learn: 0.6886929	total: 149ms	remaining: 21.2s
14:	learn: 0.6883792	total: 160ms	remaining: 21.2s
15:	learn: 0.6880698	total: 171ms	remaining: 21.2s
16:	learn: 0.6877616	total: 182ms	remaining: 21.2s
17:	learn: 0.6874522	total: 193ms	remaining: 21.2s
18:	learn: 0.6871480

FOLD 3
---------------------------------------------------


CatBoost, therefore no WandB callback.
Learning rate set to 0.012572
0:	learn: 0.6928187	total: 10.6ms	remaining: 21.2s
1:	learn: 0.6924912	total: 20.3ms	remaining: 20.3s
2:	learn: 0.6921678	total: 29.9ms	remaining: 19.9s
3:	learn: 0.6918450	total: 39.7ms	remaining: 19.8s
4:	learn: 0.6915301	total: 50.7ms	remaining: 20.2s
5:	learn: 0.6912102	total: 61.5ms	remaining: 20.4s
6:	learn: 0.6908926	total: 71.2ms	remaining: 20.3s
7:	learn: 0.6905745	total: 80.9ms	remaining: 20.2s
8:	learn: 0.6902601	total: 91.7ms	remaining: 20.3s
9:	learn: 0.6899487	total: 102ms	remaining: 20.4s
10:	learn: 0.6896348	total: 113ms	remaining: 20.5s
11:	learn: 0.6893272	total: 132ms	remaining: 21.9s
12:	learn: 0.6890165	total: 152ms	remaining: 23.2s
13:	learn: 0.6887061	total: 166ms	remaining: 23.6s
14:	learn: 0.6884023	total: 176ms	remaining: 23.3s
15:	learn: 0.6880944	total: 186ms	remaining: 23s
16:	learn: 0.6877908	total: 195ms	remaining: 22.8s
17:	learn: 0.6874864	total: 205ms	remaining: 22.6s
18:	learn: 0.687

FOLD 4
---------------------------------------------------


CatBoost, therefore no WandB callback.
Learning rate set to 0.012572
0:	learn: 0.6928226	total: 11.8ms	remaining: 23.7s
1:	learn: 0.6924947	total: 22.5ms	remaining: 22.5s
2:	learn: 0.6921660	total: 33.2ms	remaining: 22.1s
3:	learn: 0.6918403	total: 43.9ms	remaining: 21.9s
4:	learn: 0.6915252	total: 54.6ms	remaining: 21.8s
5:	learn: 0.6912066	total: 65.2ms	remaining: 21.7s
6:	learn: 0.6908902	total: 76ms	remaining: 21.6s
7:	learn: 0.6905727	total: 86.7ms	remaining: 21.6s
8:	learn: 0.6902607	total: 97.9ms	remaining: 21.7s
9:	learn: 0.6899501	total: 108ms	remaining: 21.5s
10:	learn: 0.6896347	total: 118ms	remaining: 21.3s
11:	learn: 0.6893226	total: 127ms	remaining: 21.1s
12:	learn: 0.6890121	total: 137ms	remaining: 21s
13:	learn: 0.6887001	total: 147ms	remaining: 20.8s
14:	learn: 0.6883899	total: 157ms	remaining: 20.7s
15:	learn: 0.6880826	total: 166ms	remaining: 20.6s
16:	learn: 0.6877757	total: 176ms	remaining: 20.5s
17:	learn: 0.6874688	total: 186ms	remaining: 20.5s
18:	learn: 0.68716

In [40]:
# # this loads models if you need to (or forgot to save them on training above)
# xgboost_models = {}
# xgboost_models_path = Path('/media/sf/easystore/kaggle_data/tabular_playgrounds/sep2021/models/baseline_20210905a_152521_5folds/xgboost/')
# for fold in range(5):
#     xgboost_models[fold] = load(xgboost_models_path/f'xgboost_fold{fold}_model.joblib')

# Inference

In [44]:
test_df = pd.read_csv(datapath/'test.csv', index_col='id', low_memory=False)
# test_df.to_feather(datapath/'test.feather') # issue with index being non-default; fix later
# test_df = pd.read_feather(datapath/'test.feather')

ValueError: feather does not support serializing a non-default index for the index; you can .reset_index() to make the index into column(s)

In [45]:
test_df.head()

f1        f2        f3       f4       f5       f6       f7  \
id                                                                         
957919  0.165850  0.487050   1295.00  0.02310  0.31900  0.90188   573.29   
957920  0.129650  0.373480   1763.00  0.72884  0.33247 -1.26310   875.55   
957921  0.120190  0.445210    736.26  0.04615  0.29605  0.31665  2659.50   
957922  0.054008  0.395960    996.14  0.85934  0.36678 -0.17060   386.56   
957923  0.079947 -0.006919  10574.00  0.34845  0.45008 -1.84200  3027.00   

              f8            f9       f10  ...     f109     f110    f111  \
id                                        ...                             
957919    3743.7  2.705700e+12  6221.000  ...  0.16253 -22.1890  2.0655   
957920  554370.0  5.955700e+14   934.430  ...  0.81528  -1.6342  1.5736   
957921  317140.0  3.977800e+14   131.810  ...  0.81831 -32.7800  2.1364   
957922  325680.0 -3.432200e+13   -26.473  ...  0.86559  -2.4162  1.5199   
957923  428150.0  9.291500e+11  5999.400  ...  0.25190 -18.6300  3.7387   

            f112     f113     f114    f115          f116    f117     f118  
id                                                                         
957919  0.430880 -10.7410  81606.0  1.1940  1.980400e+14  2017.1  0.46357  
957920 -1.071200  11.8320  90114.0  1.1507  4.388000e+16  6638.9  0.28125  
957921 -1.931200  -3.2804  37739.0  1.1548  1.718100e+14  5844.0  0.13797  
957922 -0.011633   1.3840  26849.0  1.1490  2.138800e+17  6173.3  0.32910  
957923  0.757080  -4.9405  50336.0  1.2488  2.151300e+17  2250.1  0.33796  

[5 rows x 118 columns]

(Here's where encapsulating the transformations in a pipeline would come in handy. But I'll do it manually for now.)

In [46]:
features = [x for x in test_df.columns if x != 'claim']
X_test = test_df[features] # this is just for naming consistency

Now, let's get the features the model was trained on and subset the test set's features accordingly

In [25]:
# generation polynomial features
# poly = PolynomialFeatures(degree=2, include_bias=True, interaction_only=False)
# X_test_poly = poly.fit_transform(X_test)

In [26]:
# X_test_poly_names = poly.get_feature_names(X_test.columns)
# X_poly_names[100:150]
# features = pd.read_csv('X_candidates_20210827.csv').columns

In [27]:
# checks = [feature in X_test_poly_names for feature in features]
# checks

In [28]:
# X_test_final = pd.DataFrame(X_test_poly, columns=X_test_poly_names)

In [29]:
# X_test_final = X_test_final[features[1:]]
# X_test_final = X_test

# Scaling
Now, going to scale using `MaxAbsScaler`

In [47]:
scaler = exmodel_config['scaler']()
X_test_scaled = scaler.fit_transform(X_test)
# X_scaled_df = pd.DataFrame(X_scaled, columns=X_poly_names)

In [49]:
xgboost_preds = {}
for fold in xgboost_models.keys():
    xgboost_preds[fold] = xgboost_models[fold].predict(X_test_scaled)

/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/data.py:112: UserWarning: Use subset (sliced data) of np.ndarray is not recommended because it will generate extra copies and increase memory consumption
  warnings.warn(


In [50]:
lightgbm_preds = {}
for fold in lightgbm_models.keys():
    lightgbm_preds[fold] = lightgbm_models[fold].predict(X_test_scaled)

In [51]:
catboost_preds = {}
for fold in catboost_models.keys():
    catboost_preds[fold] = catboost_models[fold].predict(X_test_scaled)

In [54]:
preds_path = Path(datapath/f"preds/{config_run['name']}_{exmodel_config['kfolds']}folds/")
preds_path.mkdir(exist_ok=True)

for library in ['xgboost', 'lightgbm', 'catboost']:
    (preds_path/library).mkdir(exist_ok=True)

In [56]:
dump(xgboost_preds, Path(preds_path/'xgboost/xgboost_preds_dict.joblib'))

['/media/sf/easystore/kaggle_data/tabular_playgrounds/sep2021/preds/baseline_20210905a_152521_5folds/xgboost/xgboost_preds_dict.joblib']

In [57]:
dump(lightgbm_preds, Path(preds_path/'lightgbm/lightgbm_preds_dict.joblib'))

['/media/sf/easystore/kaggle_data/tabular_playgrounds/sep2021/preds/baseline_20210905a_152521_5folds/lightgbm/lightgbm_preds_dict.joblib']

In [58]:
dump(catboost_preds, Path(preds_path/'catboost/catboost_preds_dict.joblib'))

['/media/sf/easystore/kaggle_data/tabular_playgrounds/sep2021/preds/baseline_20210905a_152521_5folds/catboost/catboost_preds_dict.joblib']

In [60]:
sample_df = pd.read_csv(datapath/'sample_solution.csv')

In [61]:
final_xgboost_preds = (xgboost_preds[0] + xgboost_preds[1] + xgboost_preds[2] + xgboost_preds[3] + xgboost_preds[4]) / 5
final_lightgbm_preds = (lightgbm_preds[0] + lightgbm_preds[1] + lightgbm_preds[2] + lightgbm_preds[3] + lightgbm_preds[4]) / 5
final_catboost_preds = (catboost_preds[0] + catboost_preds[1] + catboost_preds[2] + catboost_preds[3] + catboost_preds[4]) / 5

In [63]:
print(final_xgboost_preds[:10])
print(final_lightgbm_preds[:10])
print(final_catboost_preds[:10])

[0.  0.  0.4 0.  0.  0.  1.  0.  0.  0.8]
[0.  0.  0.2 0.  0.  0.  1.  0.  0.  1. ]
[0. 0. 0. 0. 0. 0. 1. 0. 0. 1.]


In [66]:
sample_df.loc[:, 'claim'] = final_xgboost_preds

In [67]:
sample_df.head()

id  claim
0  957919    0.0
1  957920    0.0
2  957921    0.4
3  957922    0.0
4  957923    0.0

In [68]:
submission_path = datapath/'submissions'
submission_path.mkdir(exist_ok=True)

In [69]:
sample_df.to_csv(submission_path/f"{config_run['name']}_{exmodel_config['kfolds']}folds_xgboost-mean.csv", index=False)

In [70]:
sample_df.loc[:, 'claim'] = final_lightgbm_preds
sample_df.to_csv(submission_path/f"{config_run['name']}_{exmodel_config['kfolds']}folds_lightgbm-mean.csv", index=False)

In [71]:
sample_df.loc[:, 'claim'] = final_catboost_preds
sample_df.to_csv(submission_path/f"{config_run['name']}_{exmodel_config['kfolds']}folds_catboost-mean.csv", index=False)

In [72]:
ensemble_preds = (final_xgboost_preds + final_lightgbm_preds + final_catboost_preds) / 3

In [73]:
sample_df.loc[:, 'claim'] = ensemble_preds
sample_df.to_csv(submission_path/f"{config_run['name']}_{exmodel_config['kfolds']}folds_ensemble-equal_model_and_fold_weight_mean.csv", index=False)

In [74]:
ensemble_preds = 0.4*final_xgboost_preds + 0.3*final_lightgbm_preds + 0.3*final_catboost_preds

In [75]:
sample_df.loc[:, 'claim'] = ensemble_preds
sample_df.to_csv(submission_path/f"{config_run['name']}_{exmodel_config['kfolds']}folds_ensemble-0.4xgboost_0.3lightgbm_0.3catboost-equal_fold_weight_mean.csv", index=False)

# Ensembling with CatBoost

In [46]:
catboost_models = {}
saved_models_path = Path('/home/sf/Dropbox/code_cloud/python_code/kaggle/tabular_playgrounds/aug2021/models/CatBoost_ensemble_20210831_144245_5folds/')
for fold in range(5):
    catboost_models[fold] = load(filename=Path(saved_models_path/f'catboost_fold{fold}_model.joblib'))

In [47]:
catboost_models

{0: <catboost.core.CatBoostRegressor at 0x7f1b154ecfa0>,
 1: <catboost.core.CatBoostRegressor at 0x7f1b1548a880>,
 2: <catboost.core.CatBoostRegressor at 0x7f1b154ec0a0>,
 3: <catboost.core.CatBoostRegressor at 0x7f1b1548ac40>,
 4: <catboost.core.CatBoostRegressor at 0x7f1b154ecdf0>}

In [48]:
catboost_preds = {}
for fold in catboost_models.keys():
    catboost_preds[fold] = catboost_models[fold].predict(X_test_scaled)

In [50]:
final_catboost_preds = (catboost_preds[0] + catboost_preds[1] + catboost_preds[2] + catboost_preds[3] + catboost_preds[4]) / 5

In [51]:
ensemble_preds = 0.6 * final_catboost_preds + 0.4 * final_preds

In [54]:
ensemble_preds[:10], final_catboost_preds[:10], final_preds[:10]

(array([8.40583658, 4.58774964, 8.32465697, 7.18375788, 7.13135284,
        9.67367649, 9.96252577, 5.89393404, 7.22270917, 7.53612671]),
 array([8.67110053, 4.62450053, 8.6372614 , 7.22330665, 6.92239076,
        9.70097104, 9.97590847, 5.72130089, 7.33351626, 7.44252341]),
 array([8.00794  , 4.5326233, 7.85575  , 7.1244345, 7.444796 , 9.632734 ,
        9.9424515, 6.1528835, 7.0564985, 7.6765313], dtype=float32))

In [58]:
final_ensemble_preds = 0.65 * final_catboost_preds + 0.35 * final_preds

In [59]:
final_ensemble_preds[:10], final_catboost_preds[:10], final_preds[:10]

(array([8.4389943 , 4.5923435 , 8.36373235, 7.18870129, 7.10523255,
        9.67708804, 9.96419843, 5.87235472, 7.23656006, 7.52442615]),
 array([8.67110053, 4.62450053, 8.6372614 , 7.22330665, 6.92239076,
        9.70097104, 9.97590847, 5.72130089, 7.33351626, 7.44252341]),
 array([8.00794  , 4.5326233, 7.85575  , 7.1244345, 7.444796 , 9.632734 ,
        9.9424515, 6.1528835, 7.0564985, 7.6765313], dtype=float32))

In [60]:
sample_df.loc[:, 'loss'] = final_ensemble_preds

In [61]:
sample_df.head()

id      loss
0  250000  8.438994
1  250001  4.592343
2  250002  8.363732
3  250003  7.188701
4  250004  7.105233

In [62]:
sample_df.to_csv('XGBoost0.35-Catboost0.65_ensemble_20210831_no_feature_gen.csv', index=False)

# Experiment - fitting model on full training set

In [36]:
# applying hold-out before scaling
# X_train, X_valid, y_train, y_valid = train_test_split(X, y, 
#                                                       test_size=config['test_size'], 
#                                                       random_state=config['random_state']
#                                                      )
# scaling (i.e. normalizing)
scaler = config['scaler']()
X_s = scaler.fit_transform(X)
X_test_s = scaler.fit_transform(X_test)

# selecting features
selector = config['feature_selector'](score_func=config["feature_selection_scoring"], 
                                      k=config['k_best'])
X_fs = selector.fit_transform(X_s, y)
X_test_fs = X_test_s[:, selector.get_support()]

model = XGBRegressor(
    tree_method=config['tree_method'],
    booster=config['booster'],
    n_estimators=config['n_estimators'], 
    max_depth=config['max_depth'],
    learning_rate=config['learning_rate'], 
    test_size=config['test_size'],
    subsample=config['subsample'],
    random_state=config['random_state'],
    n_jobs=config['n_jobs'], 
    verbosity=config['verbosity'], 
)
#     wandb.log({'params': model.get_params()}) # logging model parameters
model.fit(X_fs, y)#, callbacks=[wandb.xgboost.wandb_callback()])

[12:11:15] WARNING: ../src/learner.cc:573: 
Parameters: { "test_size" } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.




XGBRegressor(base_score=0.5, booster='dart', colsample_bylevel=1,
             colsample_bynode=1, colsample_bytree=1, gamma=0, gpu_id=-1,
             importance_type='gain', interaction_constraints='',
             learning_rate=0.1522, max_delta_step=0, max_depth=3,
             min_child_weight=1, missing=nan, monotone_constraints='()',
             n_estimators=400, n_jobs=-1, num_parallel_tree=1, random_state=42,
             reg_alpha=0, reg_lambda=1, scale_pos_weight=1, subsample=1,
             test_size=0.2, tree_method='auto', validate_parameters=1,
             verbosity=1)

In [37]:
y_test_preds = model.predict(X_test_fs)

/home/sf/anaconda3/envs/tabular/lib/python3.8/site-packages/xgboost/data.py:112: UserWarning: Use subset (sliced data) of np.ndarray is not recommended because it will generate extra copies and increase memory consumption
  warnings.warn(


In [38]:
sample_df = pd.read_csv(datapath/'sample_submission.csv')

In [39]:
sample_df.loc[:, 'loss'] = y_test_preds

In [40]:
sample_df.head()

id      loss
0  250000  8.027956
1  250001  4.305676
2  250002  7.300106
3  250003  6.988875
4  250004  7.316631

In [41]:
sample_df.to_csv('202108241211_XGBoost_fullset.csv', index=False)